<a href="https://colab.research.google.com/github/brianellis1997/Sarcasm_Detection/blob/Lindsey/BERT.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In this notebook, we will explore the mechanisms underlying BERT such as multi-head attention and visualize their workings. We will then perform transfer learning by freezing BERT layers and importing some basic BERT models.

In [ ]:
!git clone https://github.com/brianellis1997/Sarcasm_Detection.git

Cloning into 'Sarcasm_Detection'...
remote: Enumerating objects: 242, done.
remote: Counting objects: 100% (239/239), done.
remote: Compressing objects: 100% (177/177), done.
remote: Total 242 (delta 135), reused 115 (delta 62), pack-reused 3
Receiving objects: 100% (242/242), 7.20 MiB | 7.56 MiB/s, done.
Resolving deltas: 100% (135/135), done.


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!pip install bertviz

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 157.6/157.6 kB 3.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 139.3/139.3 kB 7.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 23.7/23.7 MB 31.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 823.6/823.6 kB 54.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.1/14.1 MB 65.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 731.7/731.7 MB 2.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 410.6/410.6 MB 3.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 121.6/121.6 MB 8.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.5/56.5 MB 11.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 124.2/124.2 MB 8.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 196.0/196.0 MB 6.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 166.0/166.0 MB 6.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━

In [ ]:
from transformers import BertModel, BertTokenizer
from bertviz import head_view
import torch

In [ ]:
import pandas as pd
train_bal = pd.read_csv('/content/drive/MyDrive/Sarcasm_Data/Train_Balanced.csv')   # Make sure path is correct in your google drive
train_bal.head()

Unnamed: 0  label                                            comment  \
0      522142      0  I personally wasn't a huge Garrosh fan, I've a...   
1      907864      1                                     you forgot the   
2      604170      1                 Nah man, she's clearly an ad carry   
3      110635      1                            This sub in a nutshell.   
4      997758      0                                       Yes... I do.   

        author        subreddit  score  ups  downs        date  \
0  cromemako83        AskReddit      2    2      0  2015-07-01   
1  _SharkWeek_        AskReddit      1    1      0  2013-03-01   
2    jdswift13  leagueoflegends      1    1      0  2015-10-01   
3    trickz-M-  GlobalOffensive      1   -1     -1  2016-12-01   
4    guriboysf           videos      4    4      0  2010-01-01   

           created_utc                                     parent_comment  
0  2015-07-11 01:55:53  Fuck Vol'jin. Garrosh Hellscream did nothing w...  
1  2013-03-14 03:03:46  That's a lie fed to you by the LIEberal media....  
2  2015-10-21 23:22:17                                  she isnt already?  
3  2016-12-05 03:50:18            Cloud 9 Qualify! (ONLY C9 FANS ALLOWED(  
4  2010-01-17 21:32:40                  "so, i hear you have a fat cock."

# Visualizing Multi-Head Attention

In [ ]:
# Let's load a vanilla BERT-base model.
tokenizer = BertTokenizer.from_pretrained('bert-base-cased')
model = BertModel.from_pretrained('bert-base-cased')

tokenizer_config.json:   0%|          | 0.00/49.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/213k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/436k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/436M [00:00<?, ?B/s]

In [ ]:
sample_text = train_bal['comment'][40]
sample_text

'Yes, lets have people nap near a person who could possibly have ebola'

In [ ]:
tokens = tokenizer.encode(sample_text)
inputs = torch.tensor(tokens).unsqueeze(0) # unsqueeze changes the shape from (20,) -> (1, 20)
inputs

tensor([[  101,  2160,   117, 11446,  1138,  1234, 22956,  1485,   170,  1825,
          1150,  1180,  3566,  1138,   174, 15792,  1161,   102]])

In [ ]:
attention = model(inputs, output_attentions=True)[2]  # Grab the attention scores from BERT

In [ ]:
# average attention in the last encoder
final_attention = attention[-1].mean(1)[0]
attention_df = pd.DataFrame(final_attention.detach()).applymap(float).round(3)

In [ ]:
attention_df.columns = tokenizer.convert_ids_to_tokens(tokens)
attention_df.index = tokenizer.convert_ids_to_tokens(tokens)

attention_df  # sums across rows add up to 1. sums across columns do not

[CLS]    Yes      ,   lets   have  people    nap   near      a  \
[CLS]     0.045  0.053  0.044  0.079  0.028   0.034  0.083  0.029  0.033   
Yes       0.008  0.073  0.018  0.026  0.018   0.014  0.023  0.009  0.010   
,         0.015  0.034  0.096  0.037  0.025   0.013  0.027  0.010  0.022   
lets      0.021  0.041  0.025  0.169  0.027   0.039  0.023  0.007  0.013   
have      0.005  0.008  0.007  0.014  0.206   0.013  0.020  0.007  0.008   
people    0.009  0.013  0.008  0.016  0.015   0.145  0.037  0.011  0.013   
nap       0.006  0.007  0.004  0.008  0.013   0.024  0.218  0.055  0.009   
near      0.004  0.005  0.005  0.006  0.004   0.007  0.020  0.210  0.009   
a         0.007  0.006  0.006  0.008  0.009   0.010  0.017  0.022  0.150   
person    0.006  0.007  0.005  0.005  0.004   0.010  0.011  0.008  0.015   
who       0.007  0.011  0.006  0.006  0.003   0.007  0.012  0.010  0.013   
could     0.005  0.006  0.004  0.007  0.005   0.007  0.007  0.005  0.011   
possibly  0.002  0.005  0.003  0.009  0.004   0.005  0.008  0.004  0.006   
have      0.001  0.003  0.002  0.002  0.002   0.004  0.006  0.004  0.005   
e         0.002  0.002  0.001  0.001  0.001   0.002  0.003  0.001  0.002   
##bol     0.002  0.004  0.002  0.003  0.002   0.003  0.005  0.002  0.003   
##a       0.004  0.010  0.003  0.004  0.002   0.005  0.007  0.004  0.007   
[SEP]     0.049  0.053  0.051  0.058  0.049   0.056  0.065  0.058  0.051   

          person    who  could  possibly   have      e  ##bol    ##a  [SEP]  
[CLS]      0.030  0.028  0.021     0.013  0.018  0.008  0.019  0.036  0.399  
Yes        0.009  0.007  0.006     0.004  0.003  0.004  0.005  0.006  0.757  
,          0.010  0.013  0.009     0.006  0.005  0.004  0.009  0.009  0.656  
lets       0.015  0.005  0.007     0.004  0.006  0.005  0.013  0.008  0.572  
have       0.004  0.002  0.003     0.003  0.003  0.001  0.003  0.003  0.691  
people     0.014  0.007  0.005     0.005  0.004  0.003  0.010  0.013  0.671  
nap        0.010  0.006  0.005     0.004  0.005  0.003  0.008  0.007  0.610  
near       0.006  0.006  0.003     0.003  0.003  0.002  0.005  0.004  0.697  
a          0.021  0.023  0.008     0.007  0.011  0.005  0.007  0.008  0.676  
person     0.195  0.026  0.009     0.005  0.011  0.006  0.024  0.015  0.638  
who        0.039  0.178  0.018     0.012  0.019  0.005  0.012  0.015  0.627  
could      0.013  0.016  0.169     0.052  0.030  0.008  0.013  0.019  0.621  
possibly   0.006  0.007  0.028     0.203  0.018  0.004  0.010  0.007  0.672  
have       0.006  0.006  0.013     0.011  0.244  0.006  0.019  0.014  0.652  
e          0.004  0.002  0.003     0.002  0.008  0.225  0.033  0.011  0.695  
##bol      0.004  0.003  0.003     0.002  0.006  0.003  0.254  0.010  0.689  
##a        0.010  0.008  0.010     0.009  0.013  0.007  0.038  0.223  0.637  
[SEP]      0.057  0.051  0.046     0.044  0.050  0.048  0.055  0.061  0.097

In [ ]:
# Layer index 2 seems to be attending to the previous token
# Layer index 6 seems to be for pronouns

tokens_as_list = tokenizer.convert_ids_to_tokens(inputs[0])
head_view(attention, tokens_as_list)

<IPython.core.display.Javascript object>

In [ ]:
# Head 3-1 attends to previous token
head_view(attention, tokenizer.convert_ids_to_tokens(inputs[0]), layer=2, heads=[0])

<IPython.core.display.Javascript object>

In [ ]:
# Head 8-10 relating direct objects to their verbs eg told -> me
head_view(attention, tokenizer.convert_ids_to_tokens(inputs[0]), layer=7, heads=[9])

<IPython.core.display.Javascript object>

In [ ]:
# attention in the 8th encoder's 10th head to see direct object attention
eight_ten = attention[7][0][9]

In [ ]:
# Get the attention matrix
attention_df = pd.DataFrame(eight_ten.detach()).applymap(float).round(3)

attention_df.columns = tokenizer.convert_ids_to_tokens(tokens)
attention_df.index = tokenizer.convert_ids_to_tokens(tokens)

attention_df  # sums across rows add up to 1. sums across columns do not

[CLS]    Yes      ,   lets   have  people    nap   near      a  \
[CLS]     0.016  0.001  0.000  0.000  0.000   0.001  0.000  0.000  0.000   
Yes       0.008  0.010  0.001  0.002  0.000   0.001  0.000  0.000  0.001   
,         0.008  0.067  0.018  0.005  0.002   0.001  0.000  0.000  0.000   
lets      0.013  0.052  0.034  0.005  0.009   0.002  0.000  0.000  0.000   
have      0.015  0.005  0.009  0.037  0.007   0.018  0.003  0.000  0.000   
people    0.031  0.003  0.006  0.018  0.020   0.014  0.004  0.001  0.000   
nap       0.011  0.000  0.001  0.004  0.012   0.034  0.065  0.003  0.001   
near      0.008  0.000  0.002  0.012  0.006   0.077  0.147  0.148  0.004   
a         0.015  0.000  0.001  0.003  0.002   0.020  0.011  0.004  0.011   
person    0.003  0.000  0.000  0.000  0.000   0.002  0.005  0.001  0.005   
who       0.020  0.000  0.001  0.000  0.001   0.009  0.018  0.007  0.064   
could     0.016  0.000  0.000  0.000  0.000   0.001  0.001  0.000  0.014   
possibly  0.009  0.001  0.000  0.001  0.000   0.001  0.001  0.002  0.039   
have      0.018  0.001  0.001  0.000  0.000   0.002  0.002  0.001  0.008   
e         0.101  0.001  0.002  0.000  0.000   0.001  0.000  0.000  0.003   
##bol     0.012  0.000  0.000  0.000  0.000   0.001  0.000  0.000  0.001   
##a       0.020  0.001  0.001  0.000  0.000   0.000  0.000  0.000  0.002   
[SEP]     0.025  0.005  0.004  0.003  0.003   0.008  0.008  0.002  0.003   

          person    who  could  possibly   have      e  ##bol    ##a  [SEP]  
[CLS]      0.000  0.000  0.000     0.000  0.000  0.000  0.000  0.000  0.980  
Yes        0.001  0.001  0.000     0.000  0.000  0.000  0.000  0.000  0.974  
,          0.000  0.001  0.000     0.000  0.000  0.000  0.000  0.000  0.897  
lets       0.000  0.001  0.000     0.000  0.000  0.000  0.000  0.001  0.879  
have       0.000  0.001  0.000     0.000  0.000  0.000  0.000  0.001  0.903  
people     0.001  0.000  0.000     0.000  0.000  0.000  0.000  0.001  0.900  
nap        0.001  0.001  0.000     0.000  0.000  0.001  0.000  0.001  0.866  
near       0.005  0.002  0.000     0.000  0.001  0.000  0.001  0.004  0.583  
a          0.009  0.002  0.000     0.000  0.000  0.000  0.000  0.003  0.919  
person     0.003  0.001  0.000     0.000  0.001  0.002  0.002  0.003  0.971  
who        0.040  0.015  0.001     0.000  0.009  0.003  0.013  0.013  0.787  
could      0.005  0.015  0.001     0.000  0.005  0.001  0.001  0.003  0.935  
possibly   0.013  0.041  0.006     0.011  0.010  0.001  0.002  0.003  0.860  
have       0.014  0.040  0.001     0.001  0.018  0.008  0.083  0.029  0.772  
e          0.004  0.006  0.002     0.000  0.022  0.011  0.002  0.008  0.837  
##bol      0.004  0.001  0.001     0.001  0.003  0.010  0.000  0.001  0.965  
##a        0.002  0.004  0.000     0.000  0.001  0.001  0.008  0.005  0.954  
[SEP]      0.002  0.003  0.002     0.004  0.005  0.004  0.002  0.003  0.915

## BERT-base

The BERT-base model we have been using has 12 stacked encoders containing 110M learnable parameters. There are other BERT sizes we might experiment with such as BERT-small which contains 4 encoders or BERT-large which contains 24. Our usage of these different sizes will depend on the processing speed of BERT-base and how fast it can work with our dataset.

In [ ]:
from transformers import BertTokenizer, BertModel
import torch
from sklearn.metrics.pairwise import cosine_similarity

In [ ]:
model = BertModel.from_pretrained('bert-base-cased')  # we are using cased BERT because of our previous analysis showing case utility in detecting sarcasm

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/436M [00:00<?, ?B/s]

In [ ]:
model #inspect the model

In [ ]:
# Get all of the model's parameters as a list of tuples.
named_params = list(model.named_parameters())

print('The BERT model has {:} different named parameters.\n'.format(len(named_params)))

print('==== Embedding Layer ====\n')
for p in named_params[0:5]:
    print("{:<55} {:>12}".format(p[0], str(tuple(p[1].size()))))

print('\n==== First Encoder ====\n')
for p in named_params[5:21]:
    print("{:<55} {:>12}".format(p[0], str(tuple(p[1].size()))))

print('\n==== Output Layer ====\n')
for p in named_params[-2:]:
    print("{:<55} {:>12}".format(p[0], str(tuple(p[1].size()))))

The BERT model has 199 different named parameters.

==== Embedding Layer ====

embeddings.word_embeddings.weight                       (28996, 768)
embeddings.position_embeddings.weight                     (512, 768)
embeddings.token_type_embeddings.weight                     (2, 768)
embeddings.LayerNorm.weight                                   (768,)
embeddings.LayerNorm.bias                                     (768,)

==== First Encoder ====

encoder.layer.0.attention.self.query.weight               (768, 768)
encoder.layer.0.attention.self.query.bias                     (768,)
encoder.layer.0.attention.self.key.weight                 (768, 768)
encoder.layer.0.attention.self.key.bias                       (768,)
encoder.layer.0.attention.self.value.weight               (768, 768)
encoder.layer.0.attention.self.value.bias                     (768,)
encoder.layer.0.attention.output.dense.weight             (768, 768)
encoder.layer.0.attention.output.dense.bias                   (768,

In [ ]:
# load the bert-base uncased tokenizer.
tokenizer = BertTokenizer.from_pretrained('bert-base-cased')

tokenizer_config.json:   0%|          | 0.00/49.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/213k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/436k [00:00<?, ?B/s]

In [ ]:
print(f'Original comment: {train_bal.comment[40]}\nTokenization using BERT: {tokenizer.encode(train_bal.comment[40])}')

Original comment: Yes, lets have people nap near a person who could possibly have ebola
Tokenization using BERT: [101, 2160, 117, 11446, 1138, 1234, 22956, 1485, 170, 1825, 1150, 1180, 3566, 1138, 174, 15792, 1161, 102]


In [ ]:
# run tokens through the model

#1 Turn tokens_with_unknown_words into a tensor (will be size (8,))
#2 Unsqueeze a first dimension to simulate batches. Resulting shape is (1, 8)
response = model(torch.tensor(tokenizer.encode(train_bal.comment[40])).unsqueeze(0))

In [ ]:
response

BaseModelOutputWithPoolingAndCrossAttentions(last_hidden_state=tensor([[[ 0.4654,  0.0803, -0.0224,  ..., -0.2867,  0.1321,  0.0760],
         [ 0.4747, -0.3772,  0.7671,  ..., -0.1184,  0.0546,  0.1523],
         [ 0.2294,  0.5972,  0.2652,  ...,  0.5398, -0.2353,  0.4644],
         ...,
         [ 0.0032,  0.1206, -0.3544,  ...,  0.3063,  0.0788, -0.6297],
         [ 0.3883,  0.1773, -0.4729,  ...,  0.0462, -0.0461,  0.2255],
         [ 1.1837,  0.5703,  0.2634,  ...,  0.1136,  0.2751, -0.1678]]],
       grad_fn=<NativeLayerNormBackward0>), pooler_output=tensor([[-0.6112,  0.3762,  0.9995, -0.9876,  0.9168,  0.9447,  0.9628, -0.9954,
         -0.9556, -0.5680,  0.9655,  0.9972, -0.9992, -0.9994,  0.8730, -0.9563,
          0.9789, -0.4363, -0.9999, -0.8351, -0.5522, -0.9995,  0.2207,  0.9842,
          0.9424,  0.0207,  0.9650,  0.9999,  0.8248, -0.5926,  0.1979, -0.9819,
          0.8948, -0.9968,  0.1323,  0.3253,  0.7783, -0.0665,  0.7855, -0.9312,
         -0.5968, -0.9198,  0.76

In [ ]:
# Embedding for each token, the first one being the [CLS] token
response.last_hidden_state

tensor([[[ 0.4654,  0.0803, -0.0224,  ..., -0.2867,  0.1321,  0.0760],
         [ 0.4747, -0.3772,  0.7671,  ..., -0.1184,  0.0546,  0.1523],
         [ 0.2294,  0.5972,  0.2652,  ...,  0.5398, -0.2353,  0.4644],
         ...,
         [ 0.0032,  0.1206, -0.3544,  ...,  0.3063,  0.0788, -0.6297],
         [ 0.3883,  0.1773, -0.4729,  ...,  0.0462, -0.0461,  0.2255],
         [ 1.1837,  0.5703,  0.2634,  ...,  0.1136,  0.2751, -0.1678]]],
       grad_fn=<NativeLayerNormBackward0>)

In [ ]:
# This layer is trained on top of the Embedding of the CLS token

response.pooler_output.shape

torch.Size([1, 768])

In [ ]:
model.pooler

BertPooler(
  (dense): Linear(in_features=768, out_features=768, bias=True)
  (activation): Tanh()
)

In [ ]:
# grab the final encoder's representation of the CLS token
CLS_embedding = response.last_hidden_state[:, 0, :].unsqueeze(0)

CLS_embedding.shape

torch.Size([1, 1, 768])

We can see that BERT-base embeddings have 768 dimensions

In [ ]:
example_phrase = tokenizer.encode(train_bal.comment[40], return_tensors='pt')
example_phrase

tensor([[  101,  2160,   117, 11446,  1138,  1234, 22956,  1485,   170,  1825,
          1150,  1180,  3566,  1138,   174, 15792,  1161,   102]])

In [ ]:
# context-less embedding of each token in our sentence
model.embeddings.word_embeddings(example_phrase)

tensor([[[ 3.3284e-02,  6.6447e-03, -3.6687e-03,  ...,  4.3273e-03,
          -8.5095e-03, -1.6365e-02],
         [ 1.4537e-04, -6.9895e-03,  4.3213e-03,  ...,  2.4379e-02,
           1.0661e-02, -2.7372e-02],
         [-4.1856e-02,  2.8818e-02, -1.6735e-02,  ...,  1.7414e-02,
          -6.3957e-02, -1.5995e-02],
         ...,
         [ 2.0032e-02, -4.0246e-04,  2.1963e-02,  ..., -7.0421e-02,
          -4.7785e-02, -1.4659e-01],
         [-4.0633e-02,  7.1398e-03, -1.0768e-02,  ..., -1.4235e-02,
          -8.6840e-02, -1.6279e-02],
         [-3.7684e-03, -4.4636e-03,  1.7056e-02,  ...,  1.5096e-02,
          -4.3010e-02,  2.8330e-02]]], grad_fn=<EmbeddingBackward0>)

In [ ]:
model.embeddings.word_embeddings(example_phrase).shape

torch.Size([1, 18, 768])

Each word in each comment will be tokenized and that token will be represented by a row containing 768 columns.

### Tokenization

In [ ]:
# Look at length of our BERT-base vocabulary
len(tokenizer.vocab)

28996

In [ ]:
# Find the index of the longest comment
longest_index = train_bal['comment'].str.len().idxmax()

# Retrieve the longest comment using the index
longest_com = train_bal.loc[longest_index, 'comment']

longest_com

'DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUMP DONALD TRUM

In [ ]:
longest_token = tokenizer.encode(longest_com)
longest_index

Token indices sequence length is longer than the specified maximum sequence length for this model (5772 > 512). Running this sequence through the model will result in indexing errors


42773

We see that BERT's tokenizer has max limits for tokens of 512.

In [ ]:
# Filter the DataFrame to include only rows where the length of the comment is greater than 500
filtered_train_bal = train_bal[train_bal['comment'].str.len() > 500]

# Calculate the number of rows in the filtered DataFrame
num_rows_with_long_comments = len(filtered_train_bal)

num_rows_with_long_comments

235

These 235 rows might present problems for our BERT model. Let's see the distribution of label.

In [ ]:
filtered_train_bal['label'].value_counts(normalize=True)

0    0.753191
1    0.246809
Name: label, dtype: float64

A significant amount of them, 75%, were non-sarcastic

## Demonstrate some Downstream Tasks

### Masked Language Modeling

In [ ]:
from transformers import BertForMaskedLM, pipeline

In [ ]:
bert_lm = BertForMaskedLM.from_pretrained('bert-base-cased')
bert_lm

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/436M [00:00<?, ?B/s]

Some weights of the model checkpoint at bert-base-cased were not used when initializing BertForMaskedLM: ['bert.pooler.dense.bias', 'bert.pooler.dense.weight', 'cls.seq_relationship.bias', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMaskedLM from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


BertForMaskedLM(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(28996, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_a

In [ ]:
nlp = pipeline('fill-mask', model='bert-base-cased')

Some weights of the model checkpoint at bert-base-cased were not used when initializing BertForMaskedLM: ['bert.pooler.dense.bias', 'bert.pooler.dense.weight', 'cls.seq_relationship.bias', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMaskedLM from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


tokenizer_config.json:   0%|          | 0.00/49.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/213k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/436k [00:00<?, ?B/s]

In [ ]:
nlp.tokenizer

BertTokenizerFast(name_or_path='bert-base-cased', vocab_size=28996, model_max_length=512, is_fast=True, padding_side='right', truncation_side='right', special_tokens={'unk_token': '[UNK]', 'sep_token': '[SEP]', 'pad_token': '[PAD]', 'cls_token': '[CLS]', 'mask_token': '[MASK]'}, clean_up_tokenization_spaces=True),  added_tokens_decoder={
	0: AddedToken("[PAD]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	100: AddedToken("[UNK]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	101: AddedToken("[CLS]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	102: AddedToken("[SEP]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	103: AddedToken("[MASK]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
}

In [ ]:
preds = nlp(f"Yes, lets have people {nlp.tokenizer.mask_token} near a person who could possibly have ebola")  # real word is 'nap'

print('Yes, lets have people *** near a person who could possibly have ebola')

for p in preds:
  print(f"Token: {p['token_str']}. Score: {100*p['score']:,.2f}%")

Yes, lets have people *** near a person who could possibly have ebola
Token: living. Score: 27.01%
Token: anywhere. Score: 11.43%
Token: live. Score: 5.78%
Token: being. Score: 3.52%
Token: sitting. Score: 3.43%


### Next Sentence Prediction

Our dataset is unique in that it contains not only the sarcastic or non-sarcastic comment, but also the parent comment which preceded it. BERT contains next sentence prediction (nsp) capability which might help us exploit this relationship and improve modeling capability.

In [ ]:
from transformers import BertForNextSentencePrediction, BertTokenizer
import torch

In [ ]:
tokenizer = BertTokenizer.from_pretrained('bert-base-cased')

bert_nsp = BertForNextSentencePrediction.from_pretrained('bert-base-cased')

In [ ]:
bert_nsp

BertForNextSentencePrediction(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(28996, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12,

In [ ]:
import numpy as np
parent_com = train_bal['parent_comment'][40]
com = train_bal['comment'][40]

print(parent_com)
print(com)

You know how people who work around the clock at hospitals during emergencies have staff rooms where they can go and nap? Like that.
Yes, lets have people nap near a person who could possibly have ebola


In [ ]:
inputs = tokenizer(parent_com, com, return_tensors='pt')
inputs

{'input_ids': tensor([[  101,  1192,  1221,  1293,  1234,  1150,  1250,  1213,  1103,  4705,
          1120,  8894,  1219, 12982,  9885,  1138,  2546,  4045,  1187,  1152,
          1169,  1301,  1105, 22956,   136,  2409,  1115,   119,   102,  2160,
           117, 11446,  1138,  1234, 22956,  1485,   170,  1825,  1150,  1180,
          3566,  1138,   174, 15792,  1161,   102]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]])}

In [ ]:
# 0 == next sentence and 1 == not next sentence
outputs = bert_nsp(**inputs)

outputs

NextSentencePredictorOutput(loss=None, logits=tensor([[ 5.2431, -5.9602]], grad_fn=<AddmmBackward0>), hidden_states=None, attentions=None)

In [ ]:
outputs = bert_nsp(**inputs, labels=torch.LongTensor([0]))
outputs

NextSentencePredictorOutput(loss=tensor(1.3590e-05, grad_fn=<NllLossBackward0>), logits=tensor([[ 5.2431, -5.9602]], grad_fn=<AddmmBackward0>), hidden_states=None, attentions=None)

The loss is very low which means our bert base model is very confident that these two sentences are connected which is good. This connection between parent comment and child comment might help us classify things better with this BERT capability.<br>We can analyze the places where the nsp confidence is low and see if there's any correlation between confidence and label.

## Sequence Classification

In [ ]:
!pip install datasets

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 510.5/510.5 kB 5.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 7.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 11.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 9.9 MB/s eta 0:00:00


In [ ]:
from transformers import Trainer, TrainingArguments, DistilBertForSequenceClassification, DistilBertTokenizerFast, \
     DataCollatorWithPadding, pipeline
from datasets import load_metric, Dataset
import numpy as np
from sklearn.preprocessing import LabelEncoder

In [ ]:
# conjoin comment and parent comment
train_bal['joined_comment'] = 'parent_comment: ' + train_bal['parent_comment'] + ' child_comment: ' + train_bal['comment']
# here we are concatenating the comment to the parent comment and providing context for our LLM model by prompting the parent comment and child comment locations.

train_bal.head()

Unnamed: 0  label                                            comment  \
0      522142      0  I personally wasn't a huge Garrosh fan, I've a...   
1      907864      1                                     you forgot the   
2      604170      1                 Nah man, she's clearly an ad carry   
3      110635      1                            This sub in a nutshell.   
4      997758      0                                       Yes... I do.   

        author        subreddit  score  ups  downs        date  \
0  cromemako83        AskReddit      2    2      0  2015-07-01   
1  _SharkWeek_        AskReddit      1    1      0  2013-03-01   
2    jdswift13  leagueoflegends      1    1      0  2015-10-01   
3    trickz-M-  GlobalOffensive      1   -1     -1  2016-12-01   
4    guriboysf           videos      4    4      0  2010-01-01   

           created_utc                                     parent_comment  \
0  2015-07-11 01:55:53  Fuck Vol'jin. Garrosh Hellscream did nothing w...   
1  2013-03-14 03:03:46  That's a lie fed to you by the LIEberal media....   
2  2015-10-21 23:22:17                                  she isnt already?   
3  2016-12-05 03:50:18            Cloud 9 Qualify! (ONLY C9 FANS ALLOWED(   
4  2010-01-17 21:32:40                  "so, i hear you have a fat cock."   

                                      joined_comment  
0  parent_comment: Fuck Vol'jin. Garrosh Hellscre...  
1  parent_comment: That's a lie fed to you by the...  
2  parent_comment: she isnt already? child_commen...  
3  parent_comment: Cloud 9 Qualify! (ONLY C9 FANS...  
4  parent_comment: "so, i hear you have a fat coc...

In [ ]:
train_bal['joined_comment'][0]

"parent_comment: Fuck Vol'jin. Garrosh Hellscream did nothing wrong. If Vol'jin actually took the time to help Garrosh instead of instantly turning on him and starting a rebellion, the Horde would be in a better place. That goes for all the other leaders and advisers too. Garrosh wouldn't have turned to a *Blackrock* orc if people didn't immediately hate him for being chosen to be Warchief. Long live Hellscream. In life and through death. child_comment: I personally wasn't a huge Garrosh fan, I've always loved the Tauren and Trolls."

In [ ]:
# Filter the DataFrame to include only rows where the length of the comment is greater than 500
filtered_train_bal = train_bal[train_bal['joined_comment'].str.len() > 500]

# Calculate the number of rows in the filtered DataFrame
num_rows_with_long_comments = len(filtered_train_bal)

num_rows_with_long_comments

46588

In [ ]:
# This code segment parses our dataset into a more manageable format

utterances = train_bal['joined_comment']
sequence_labels = train_bal['label']

In [ ]:
len(utterances), len(sequence_labels)

(808618, 808618)

In [ ]:
tokenizer = DistilBertTokenizerFast.from_pretrained('distilbert-base-cased')

tokenizer_config.json:   0%|          | 0.00/29.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/213k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/436k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/465 [00:00<?, ?B/s]

In [ ]:
unique_sequence_labels = list(set(sequence_labels))
unique_sequence_labels

[0, 1]

In [ ]:
sequence_labels = [unique_sequence_labels.index(l) for l in sequence_labels]

print(f'There are {len(unique_sequence_labels)} unique sequence labels')

There are 2 unique sequence labels


In [ ]:
sarc_dataset = Dataset.from_dict(
    dict(
        utterance=utterances,
        label=sequence_labels
    )
)
sarc_dataset = sarc_dataset.train_test_split(test_size=0.2)

In [ ]:
sarc_dataset['train'][0]

{'utterance': 'parent_comment: In this case you can also hit esc to cancel and cmd-d for don\'t save. child_comment: OK, so rename the extension of a file... Now you\'ll have to use the mouse to click the "Use .newextension", and like this one there are a lot more actions that require this interaction.',
 'label': 0}

In [ ]:
# simple function to batch tokenize utterances with truncation
def preprocess_function(examples):
    return tokenizer(examples["utterance"], truncation=True)  # Truncation will solve the problem of longer than 512 length tokens

In [ ]:
seq_clf_tokenized_sarc = sarc_dataset.map(preprocess_function, batched=True)

Map:   0%|          | 0/646894 [00:00<?, ? examples/s]

Map:   0%|          | 0/161724 [00:00<?, ? examples/s]

In [ ]:
seq_clf_tokenized_sarc['train'][0]

{'utterance': 'parent_comment: In this case you can also hit esc to cancel and cmd-d for don\'t save. child_comment: OK, so rename the extension of a file... Now you\'ll have to use the mouse to click the "Use .newextension", and like this one there are a lot more actions that require this interaction.',
 'label': 0,
 'input_ids': [101,
  6486,
  168,
  7368,
  131,
  1130,
  1142,
  1692,
  1128,
  1169,
  1145,
  1855,
  13936,
  1665,
  1106,
  19722,
  1105,
  3975,
  1181,
  118,
  173,
  1111,
  1274,
  112,
  189,
  3277,
  119,
  2027,
  168,
  7368,
  131,
  10899,
  117,
  1177,
  1231,
  16124,
  1103,
  4973,
  1104,
  170,
  4956,
  119,
  119,
  119,
  1986,
  1128,
  112,
  1325,
  1138,
  1106,
  1329,
  1103,
  10322,
  1106,
  13440,
  1103,
  107,
  11696,
  119,
  1207,
  11708,
  23826,
  1988,
  107,
  117,
  1105,
  1176,
  1142,
  1141,
  1175,
  1132,
  170,
  1974,
  1167,
  3721,
  1115,
  4752,
  1142,
  8234,
  119,
  102],
 'attention_mask': [1,
  1,
  1,


In [ ]:
# DataCollatorWithPadding creates batch of data. It also dynamically pads text to the
#  length of the longest element in the batch, making them all the same length.
#  It's possible to pad your text in the tokenizer function with padding=True, dynamic padding is more efficient.

data_collator = DataCollatorWithPadding(tokenizer=tokenizer)

Data Collator will pad data so that all examples are the same input length.
Attention mask is how we ignore attention scores for padding tokens

In [ ]:
sequence_clf_model = DistilBertForSequenceClassification.from_pretrained(
    'distilbert-base-cased',
    num_labels=len(unique_sequence_labels),
)

# set an index -> label dictionary
sequence_clf_model.config.id2label = {i: l for i, l in enumerate(unique_sequence_labels)}

model.safetensors:   0%|          | 0.00/263M [00:00<?, ?B/s]

Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-cased and are newly initialized: ['classifier.bias', 'classifier.weight', 'pre_classifier.bias', 'pre_classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [ ]:
sequence_clf_model.config.id2label[0]

0

In [ ]:
metric = load_metric("accuracy")

def compute_metrics(eval_pred):  # custom method to take in logits and calculate accuracy of the eval set
    logits, labels = eval_pred
    predictions = np.argmax(logits, axis=-1)
    return metric.compute(predictions=predictions, references=labels)

<ipython-input-42-9070dabc94cd>:1: FutureWarning: load_metric is deprecated and will be removed in the next major version of datasets. Use 'evaluate.load' instead, from the new library 🤗 Evaluate: https://huggingface.co/docs/evaluate
  metric = load_metric("accuracy")
/usr/local/lib/python3.10/dist-packages/datasets/load.py:756: FutureWarning: The repository for accuracy contains custom code which must be executed to correctly load the metric. You can inspect the repository content at https://raw.githubusercontent.com/huggingface/datasets/2.18.0/metrics/accuracy/accuracy.py
You can avoid this message in future by passing the argument `trust_remote_code=True`.
Passing `trust_remote_code=True` will be mandatory to load this metric from the next major release of `datasets`.
  warnings.warn(


In [71]:
epochs = 2

training_args = TrainingArguments(
    output_dir="./sarc/results",
    num_train_epochs=epochs,
    per_device_train_batch_size=32,
    per_device_eval_batch_size=32,
    load_best_model_at_end=True,

    # some deep learning parameters that the Trainer is able to take in
    warmup_steps=len(seq_clf_tokenized_sarc['train']) // 5,  # number of warmup steps for learning rate scheduler,
    weight_decay = 0.05,

    logging_steps=1,
    log_level='info',
    evaluation_strategy='epoch',
    eval_steps=50,
    save_strategy='epoch'
)

# Define the trainer:

trainer = Trainer(
    model=sequence_clf_model,
    args=training_args,
    train_dataset=seq_clf_tokenized_sarc['train'],
    eval_dataset=seq_clf_tokenized_sarc['test'],
    compute_metrics=compute_metrics,
    data_collator=data_collator
)

/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:432: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(


<ipython-input-68-32b6ab62b2dd>:2: FutureWarning: load_metric is deprecated and will be removed in the next major version of datasets. Use 'evaluate.load' instead, from the new library 🤗 Evaluate: https://huggingface.co/docs/evaluate
  metric = load_metric("accuracy")  # custom method to take in logits and calculate accuracy of the eval set
/usr/local/lib/python3.10/dist-packages/datasets/load.py:756: FutureWarning: The repository for accuracy contains custom code which must be executed to correctly load the metric. You can inspect the repository content at https://raw.githubusercontent.com/huggingface/datasets/2.18.0/metrics/accuracy/accuracy.py
You can avoid this message in future by passing the argument `trust_remote_code=True`.
Passing `trust_remote_code=True` will be mandatory to load this metric from the next major release of `datasets`.
  warnings.warn(


/usr/local/lib/python3.10/dist-packages/datasets/load.py:756: FutureWarning: The repository for accuracy contains custom code which must be executed to correctly load the metric. You can inspect the repository content at https://raw.githubusercontent.com/huggingface/datasets/2.18.0/metrics/accuracy/accuracy.py
You can avoid this message in future by passing the argument `trust_remote_code=True`.
Passing `trust_remote_code=True` will be mandatory to load this metric from the next major release of `datasets`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/datasets/load.py:756: FutureWarning: The repository for accuracy contains custom code which must be executed to correctly load the metric. You can inspect the repository content at https://raw.githubusercontent.com/huggingface/datasets/2.18.0/metrics/accuracy/accuracy.py
You can avoid this message in future by passing the argument `trust_remote_code=True`.
Passing `trust_remote_code=True` will be mandatory to load this metric 

KeyboardInterrupt: 